# Unity Catalog: Data Monitoring

## Bloque 9: Monitor de Series Temporales - DEMO


### 9.0 Caso de uso
Analicemos un caso de uso en el sector minorista, donde una de las capas más importantes es la tabla `silver_transaction`, que combina datos de las tablas *bronze* de origen y afecta a las tablas *gold* posteriores.  
El esquema de datos utilizado en la demostración es el siguiente:

<img src="https://raw.githubusercontent.com/databricks-demos/dbdemos-resources/main/images/product/lhm/lhm_data.png" width="600px"/>

Los analistas de datos utilizan estas tablas para generar informes y tomar diversas decisiones empresariales.  
Recientemente, un analista intenta determinar el `PreferredPaymentMethod` más popular.  
Al consultar la tabla `silver_transaction`, descubre que existe un número considerable de transacciones con `PreferredPaymentMethod` en `null`, y comparte una captura del problema:

![image3](https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/lhm/lhm_payment_type.png?raw=true)

En este punto, es posible que te plantees varias preguntas, como por ejemplo:  
1. ¿Qué porcentaje de valores `null` se ha introducido en esta columna? ¿Es algo habitual?  
2. Si no lo es, ¿cuál fue la causa raíz de este problema de integridad?  
3. ¿Qué activos descendentes podrían haberse visto afectados por este problema?

### 9.1 Dependencias para el ejercicio

In [0]:
%pip install databricks-sdk==0.40.0
%restart_python

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 629.7/629.7 kB 13.8 MB/s eta 0:00:00
  Attempting uninstall: databricks-sdk
    Found existing installation: databricks-sdk 0.49.0
    Not uninstalling databricks-sdk at /databricks/python3/lib/python3.12/site-packages, outside environment /local_disk0/.ephemeral_nfs/envs/pythonEnv-45c14402-488a-43b3-9250-bbf5a5b1b17c
    Can't uninstall 'databricks-sdk'. No files were found to uninstall.
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
databricks-connect 17.2.2 requires databricks-sdk>=0.46.0, but you have databricks-sdk 0.40.0 which is incompatible.
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
dbutils.notebook.run("./src/08_DataGeneration", 0)


### 9.2 Vemos el Data Set

In [0]:
%sql 
-- To setup monitoring, load in the silver_transaction dataset
SELECT * from silver_transaction limit 10;

ProductID UserID TransactionID TransactionDate Quantity UnitPrice TotalPrice PaymentMethod ShippingAddress LoyaltyPointsEarned GiftWrap SpecialInstructions Username Email PasswordHash FullName DateOfBirth Gender PhoneNumber Address City State Country PostalCode RegistrationDate LastLoginDate AccountStatus UserRole PreferredPaymentMethod TotalPurchaseAmount NewsletterSubscription Wishlist CartItems ProductName Category SubCategory Brand Description Price Discount StockQuantity SKU ProductImageURL ProductRating NumberOfReviews SupplierID DateAdded Dimensions Weight Color Material WarrantyPeriod ReturnPolicy ShippingCost ProductTags TempDate Campaign_flag 53b53445-bb17-4b3c-ad66-74282ec5acf1 d48e39e3-d9ef-4a19-a4a1-82502ea874a3 8f9dc242-7964-4da4-ac2f-30a8695bc16c 2025-10-02T16:37:57.194Z 1.0 1915.98 1915.97998046875 PayPal 8856 Patrick Center
Alisontown, KY 64161 192 no Set respond fact ready as nation. bryantkimberly mccoylindsay@example.com d84ecdcd82793490325b216f2acf11484b8db913502481114806f5738222003b Jessica Frazier 2005-11-15 Other 309-257-8705 8856 Patrick Center
Alisontown, KY 64161 Berrymouth Hawaii Egypt 33494 2025-03-25 2025-08-18 Suspended Customer PayPal 547.81 true List(8059962e-881c-4501-8394-f7ad859b5df4, d0c6e50d-c9ff-48ef-93fe-7d93fd456acb) List(5bddf4a6-a05e-4c58-815f-7541d298f737) Cookbook Books Non-Fiction BrandR Engaging story that captivates readers. 1915.98 0.0 226 YnV-33115378 https://placekitten.com/399/2 3.4000000953674316 1492 36ac73f6-1738-4369-8d78-b5b13bac9574 2025-10-07 88.41 x 58.84 x 11.04 36.58 DarkOrange Plastic 2 months 30 days 25.9 List(five, artist, PM) 2025-10-02 false ec9abeae-0b13-4250-8fe5-d391519e02fe 23e810c0-7272-413f-a9f5-4654db0777fe 0897b8c3-2d87-427a-9dbb-98bfa07e3e06 2025-10-02T00:00:11.453Z 4.0 691.84 2767.360107421875 Credit Card 096 Gonzalez Spurs Apt. 741
Lake Marc, IA 30826 277 null steven36 xjohnson@example.com c0c28d7dc1110a4a33939071df6fb918d44ed09a3f2f582e6560f02e6890a310 Brandon Adams 1997-03-18 Female 001-847-339-2537x610 096 Gonzalez Spurs Apt. 741
Lake Marc, IA 30826 Sarahton Utah Mexico 20290 2021-08-13 2025-05-27 Active Customer Bank Transfer 4124.46 true List(7c0e1b02-b290-4146-86d9-05d88b84f5ca, 36ff3679-9174-4def-bdd9-a85ad54b111e, f077f171-540d-4dc4-bf5f-36b8ef04d106, 96b6dc90-1ce6-4596-b13b-b10b2f5f4d63, cb74df82-4b53-42bc-a1c0-bf9ee6b705c7, 5a2a1a39-8110-422c-bf16-38d82231bbe3, 7dd318bb-da10-4262-a194-d3d355e0254c) List(a176972f-8a12-4d87-8cd7-f127d95b8d04) Cutting Board Home & Kitchen Bedding BrandGG Essential appliance for modern homes. 691.84 0.25 597 oKS-46512038 https://picsum.photos/738/985 2.9000000953674316 524 3fa7c535-f9e0-4275-9799-c7db867c7712 2024-04-04 28.56 x 32.97 x 69.92 46.49 PaleTurquoise Plastic 24 months 60 days 10.86 null 2025-10-02 false af734fb5-076e-4454-9379-13d0b4376cb9 8f7ede44-518d-410f-94df-200300601f83 8bcd2ff8-5c09-41e4-86c0-4cbff06a3906 2025-10-02T05:35:39.062Z 4.0 497.01 1988.0400390625 Credit Card 2604 Peterson Branch
Justinburgh, UT 23678 199 yes Yourself management may choice particularly order. harolddavis royrobin@example.org 104ff6d71c7fbd29a5aa69b4b672fd83845649afce7b808276a2437906d06bda Pamela Wilson 1938-09-14 Male 416-918-2710 2604 Peterson Branch
Justinburgh, UT 23678 South Lauraberg New Mexico Suriname 25861 2020-07-07 2025-08-21 Inactive Admin Bank Transfer 3780.42 true List() List(7a92f37d-267e-4a83-85d9-47181cd38e8e, b478241d-7168-4cec-a8f3-75caf29e2a27, a274a939-b2b9-435f-aad7-f2cb81f64f91, 6a68ac6f-4246-4f5b-8f28-a990f8e5a5fa, 78b2d1b8-7ad4-49aa-ba74-660e6bb3a6fe) Building Blocks Toys Puzzles BrandVV Safe and durable materials. 497.01 0.0 2 eMd-45375023 https://placekitten.com/774/668 3.200000047683716 4306 44ca6767-7f28-4602-bdbe-cb0796ef6a16 2024-09-24 56.74 x 25.08 x 70.06 1.45 Gold Plastic 6 months No returns 26.95 List(keep, he) 2025-10-02 false 0af011c7-f021-4689-99ed-e6d105d88910 1cdcdc93-5d2e-4448-9ce0-f5df2840d3cd 371f1866-6c63-42c2-8dfb-2c18f1984a4c 2025-10-02T19:22:48.037Z 2.0 1793.29 3586.580078

### 9.3 Crear el Monitoring

Un Lakehouse Monitor analiza periódicamente una tabla (normalmente una Gold o Silver) y genera métricas como:

- Distribuciones de columnas (mean, std, min, max, nulls, etc.)
- Detección de data drift (comparar cómo cambian los datos entre días/horas)
- Detección de anomalías en series temporales
- Conteo de outliers, duplicados, tipos erróneos
- Freshness (tiempo desde la última actualización)

Databricks crea internamente:
- Un objeto “Lakehouse Monitor” vinculado a esa tabla.
- Dos tablas de resultados:
    - ``_profile_metrics`` → estadísticas por columna.
    - ``_drift_metrics`` → comparación temporal entre periodos.
- Un schedule para refrescar esas métricas.
- Un dashboard autogenerado (visible desde Catalog → Quality).

Para crear un Monitoring, podemos elegir entre tres tipos de perfiles diferentes:  
1. **Timeseries**: agrega métricas de calidad a lo largo de ventanas de tiempo.  
2. **Snapshot**: calcula métricas de calidad sobre toda la tabla.  
3. **Inference**: realiza un seguimiento del desplazamiento del modelo (*model drift*) y su rendimiento a lo largo del tiempo.  

Dado que estamos monitorizando datos de transacciones y la tabla contiene una columna de marca de tiempo, el tipo *Timeseries* es el más adecuado para este caso.  
Para otros tipos de análisis, consulta la documentación de Lakehouse Monitoring ([AWS](https://docs.databricks.com/en/lakehouse-monitoring/create-monitor-ui.html#profiling) | [Azure](https://learn.microsoft.com/en-us/azure/databricks/lakehouse-monitoring/create-monitor-ui#profiling)).

In [0]:
from databricks.sdk import WorkspaceClient
from databricks.sdk.service.catalog import MonitorTimeSeries
import os

In [0]:
# Define ventanas de tiempo para agregar métricas durante
GRANULARITIES = ["1 day"]                       

# Opcionalmente, define expresiones para segmentar los datos con
SLICING_EXPRS = ["Category='Toys'"]  

In [0]:
# Debe tener privilegios `USE CATALOG` sobre el catálogo y debe tener privilegios `USE SCHEMA` sobre el esquema.
TABLE_NAME = f"{catalog}.{dbName}.silver_transaction"

# Define la columna de time_Stamp
TIMESTAMP_COL = "TransactionDate"

# Habilitar la fuente de datos de cambios (CDF) para procesar incrementalmente los cambios en la tabla y lograr una ejecución más eficiente
display(spark.sql(f"ALTER TABLE {TABLE_NAME} SET TBLPROPERTIES (delta.enableChangeDataFeed = true)"))

In [0]:
# Crea un monitor utilizando un perfil de tipo Serie temporal. Una vez completada la actualización inicial, podrás ver el panel generado automáticamente en la pestaña Calidad de la tabla en el Explorador de catálogos.
print(f"Creating monitor for {TABLE_NAME}")

w = WorkspaceClient()

try:
  lhm_monitor = w.quality_monitors.create(
    table_name=TABLE_NAME, # Always use 3-level namespace
    time_series = MonitorTimeSeries(
      timestamp_col=TIMESTAMP_COL,
      granularities=GRANULARITIES
    ),
    assets_dir = f"{os.getcwd()}/monitoring",
    output_schema_name=f"{catalog}.{dbName}"
  )
  
except Exception as lhm_exception:
  if "already exist" in str(lhm_exception).lower():
    print(f"Monitor for {TABLE_NAME} already exists, retrieving monitor info:")
    lhm_monitor = w.quality_monitors.get(table_name=f"{TABLE_NAME}")

  else:
    raise lhm_exception

Creating monitor for main_monitoring.demo_monitoring.silver_transaction


El siguiente paso espera a que se cree el monitor y, a continuación, a que finalice el cálculo inicial de las métricas.

Nota: La creación y actualización del monitor puede tardar más de 10 minutos.

In [0]:
import time
from databricks.sdk.service.catalog import MonitorInfoStatus, MonitorRefreshInfoState

In [0]:
# Wait for monitor to be created
lhm_monitor = w.quality_monitors.get(table_name=f"{TABLE_NAME}")
while lhm_monitor.status == MonitorInfoStatus.MONITOR_STATUS_PENDING:
  lhm_monitor = w.quality_monitors.get(table_name=f"{TABLE_NAME}")
  time.sleep(10)

assert lhm_monitor.status == MonitorInfoStatus.MONITOR_STATUS_ACTIVE, "Error creating monitor"

refreshes = w.quality_monitors.list_refreshes(table_name=f"{TABLE_NAME}").refreshes
assert(len(refreshes) > 0)

run_info = refreshes[0]
while run_info.state in (MonitorRefreshInfoState.PENDING, MonitorRefreshInfoState.RUNNING):
  run_info = w.quality_monitors.get_refresh(table_name=f"{TABLE_NAME}", refresh_id=run_info.refresh_id)
  time.sleep(30)

assert run_info.state == MonitorRefreshInfoState.SUCCESS, "Monitor refresh failed"

### 9.4 Orientación sobre la tabla de métricas de perfil


Esta tabla contiene las estadísticas que genera el monitor de calidad sobre tu tabla (por ejemplo: medias, nulos, desviaciones, etc.).  
Cada fila representa una combinación de **columna + periodo de tiempo + grupo (slice)**. 



---

#### Columnas principales

| Columna | Descripción |
|----------|-------------|
| **log_type** | Indica de dónde vienen los datos:<br>- `INPUT`: estadísticas de la tabla actual.<br>- `BASELINE`: estadísticas de referencia (la tabla con la que se compara). |
| **column_name** | Nombre de la columna analizada. Si el valor es `:table`, la métrica se calcula sobre toda la tabla (por ejemplo, número total de filas). |
| **granularity** | Solo aparece en monitores de tipo *TimeSeries*. Indica la granularidad temporal (por ejemplo, `1 day`). En las filas de `BASELINE` aparece como `null`. |
| **window** | Muestra el periodo temporal específico (por ejemplo, `2025-10-31`). En las filas de `BASELINE` aparece como `null`. |
| **slice_key / slice_value** | Si el monitor divide los datos en grupos (por ejemplo, por país o región), estas columnas indican el nombre del grupo y su valor. Si no hay agrupación, ambos aparecen como `null`. |

---

#### Interpretación

Cada fila indica algo del estilo:

> Para la columna X, en el periodo Y y (si aplica) en el grupo Z, las estadísticas calculadas fueron las siguientes (media, nulos, etc.).

Las filas con:
- `log_type = BASELINE` → métricas de referencia.  
- `column_name = :table` → métricas globales (no asociadas a una columna concreta).


In [0]:
# Display profile metrics table
profile_table = lhm_monitor.profile_metrics_table_name  
display(spark.sql(f"SELECT * FROM {profile_table}"))

window log_type logging_table_commit_version monitor_version granularity slice_key slice_value column_name count data_type num_nulls avg quantiles min max stddev num_zeros num_nan min_length max_length avg_length non_null_columns frequent_items median distinct_count percent_nan percent_null percent_zeros percent_distinct List(2025-10-02T00:00:00.000Z, 2025-10-03T00:00:00.000Z) INPUT 2 0 1 day null null AccountStatus 51 string 0 null null null null null null null 6.0 9.0 7.980392156862745 null List(List(Suspended, 23), List(Inactive, 16), List(Active, 12)) null 3 null 0.0 null 5.88235294117647 List(2025-10-02T00:00:00.000Z, 2025-10-03T00:00:00.000Z) INPUT 2 0 1 day null null Address 51 string 0 null null null null null null null 23.0 56.0 43.88235294117647 null List(List(03900 Rebekah Rapid Apt. 758
Laurenstad, NE 82320, 1), List(435 Clark Hill Apt. 841
Lindsayborough, CA 22013, 1), List(1759 Alec Viaduct Suite 728
Danielbury, NY 83097, 1), List(136 Norman Gardens Suite 216
Marksborough, SD 30466, 1), List(158 Benton Junctions Suite 000
East Wendy, NJ 49833, 1), List(PSC 8617, Box 9839
APO AE 22526, 1), List(7618 Roy Expressway Apt. 041
Sarahburgh, GA 57534, 1), List(PSC 5095, Box 6192
APO AP 38311, 1), List(395 Jacob Manors
Lake Terrance, AR 52710, 1), List(4833 Riley Dale Suite 499
West Logan, ID 94547, 1), List(8856 Patrick Center
Alisontown, KY 64161, 1), List(97558 Kimberly Rapid
East Nancyland, IA 08027, 1), List(52247 Rachel Drives
West Melissa, VT 97120, 1), List(6854 Gonzales Prairie
Bradleyhaven, VA 17620, 1), List(2165 Rodgers Mall Suite 422
West Christinafort, LA 08421, 1), List(9278 Cindy Key Suite 146
Newtonburgh, MS 83456, 1), List(62864 Denise Radial
South Steven, CO 50970, 1), List(912 Keith Mountains Apt. 530
Howellhaven, CA 73189, 1), List(PSC 6962, Box 6473
APO AP 64644, 1), List(670 Ashley Village
North Vanessahaven, ID 92187, 1), List(20248 Frazier Village Suite 135
South Albert, MA 06385, 1), List(7845 Shannon Estates
New Rachel, GA 76404, 1), List(3186 Brittany Valleys
Sarahview, SC 18798, 1), List(PSC 2866, Box 1568
APO AA 50293, 1), List(294 Adams Club Suite 078
Christinastad, CT 67363, 1), List(USNV Drake
FPO AE 32607, 1), List(52320 Smith Crescent Apt. 650
Johnsonhaven, OR 97370, 1), List(10185 Juarez Crescent
Lake Jeanetteport, PR 23050, 1), List(94743 Collier Plaza Apt. 303
Mejiachester, NE 67038, 1), List(4991 Rebecca Circles Suite 193
Powellbury, KY 00953, 1), List(969 Ford Port Apt. 741
Wendyfurt, SD 64592, 1), List(5681 Wright Rapid Apt. 119
Smithport, CO 31460, 1), List(026 Foster Greens Apt. 697
East Jessicaberg, DC 66309, 1), List(PSC 0001, Box 7610
APO AA 16134, 1), List(191 Hall Mill
Evansside, ME 43087, 1), List(0920 Jones Cliff Apt. 764
North Williamville, WI 04185, 1), List(538 Cynthia Skyway
Hollyborough, DC 58393, 1), List(79765 Bell Mission
West Claire, AK 31385, 1), List(67721 Morgan Pine Suite 930
Cartermouth, WA 02783, 1), List(01722 Kevin Road Suite 908
Lake Nicholasport, OH 29991, 1), List(USS Nelson
FPO AE 08610, 1), List(49630 Davis Inlet
Briannaton, CO 68520, 1), List(098 Murphy Unions
Robynbury, PR 02681, 1), List(885 Jared Turnpike Apt. 098
Evanschester, MS 33199, 1), List(41903 Wiley Ville Apt. 147
Valentineport, NM 94575, 1), List(3200 Gentry Circles Suite 640
Port Rebecca, AL 65850, 1), List(3504 Dawn Prairie
Jenniferton, GU 96947, 1), List(70108 Kelsey Haven Suite 995
North Matthew, AL 04333, 1), List(1926 Amy Cape
North Vincent, GA 18647, 1), List(0270 Yates Path Apt. 706
New Debrafort, SC 60325, 1), List(7665 Robinson Shoals
Port Cindy, UT 25088, 1)) null 50 null 0.0 null 98.0392156862745 List(2025-10-02T00:00:00.000Z, 2025-10-03T00:00:00.000Z) INPUT 2 0 1 day null null Brand 51 string 0 null null null null null null null 6.0 7.0 6.352941176470588 null List(List(BrandB, 4), List(BrandO, 3), List(BrandR, 3), List(BrandBB, 3), List(BrandT, 2), List(BrandJ, 2), List(BrandKK, 2), List(BrandS, 2), List(BrandA, 2), List(BrandG, 2), List(BrandMM, 2), List(BrandTT, 2), List(B

### 9.5 Orientacion sobre la tabla `_drift_metrics`

Esta tabla contiene las métricas que muestran **cómo cambian los datos con el tiempo** o **respecto a una tabla de referencia (baseline)**.  
Cada fila representa una combinación de **columna + periodo de tiempo + grupo (slice)**.

---

#### Columnas principales

| Columna | Descripción |
|----------|-------------|
| **drift_type** | Indica con qué se compara la tabla actual:<br>- `CONSECUTIVE`: comparación con la ventana temporal anterior.<br>- `BASELINE`: comparación con la tabla de referencia. |
| **column_name** | Nombre de la columna analizada. Si el valor es `:table`, la métrica se calcula sobre toda la tabla (por ejemplo, número total de filas o tasa de cambio global). |
| **granularity** | Solo aparece en monitores de tipo *TimeSeries*. Indica la granularidad temporal (por ejemplo, `1 day`). |
| **window** | Ventana temporal de los datos actuales (por ejemplo, `2025-10-31`). |
| **window_cmp** | Ventana con la que se hace la comparación. Si la comparación es con la tabla de referencia, este valor aparece como `null`. |
| **slice_key / slice_value** | Si el monitor agrupa los datos (por ejemplo, por país o categoría), estas columnas indican el grupo y su valor. Si no hay agrupación, ambos aparecen como `null`. |

---

#### Interpretación

Cada fila indica algo del estilo:

> Para la columna X, en la ventana Y, comparada con la ventana Z (o con la baseline), las métricas de deriva calculadas fueron las siguientes.

Las filas con:
- `drift_type = CONSECUTIVE` → comparan una ventana con la anterior.  
- `drift_type = BASELINE` → comparan con la tabla de referencia.  
- `column_name = :table` → métricas globales, no asociadas a una columna concreta.


In [0]:
# Display the drift metrics table
drift_table = lhm_monitor.drift_metrics_table_name  
display(spark.sql(f"SELECT * FROM {drift_table}"))

window granularity monitor_version slice_key slice_value column_name data_type window_cmp drift_type count_delta avg_delta percent_null_delta percent_zeros_delta percent_distinct_delta non_null_columns_delta js_distance ks_test wasserstein_distance population_stability_index chi_squared_test tv_distance l_infinity_distance List(2025-10-09T00:00:00.000Z, 2025-10-10T00:00:00.000Z) 1 day 0 null null :table null List(2025-10-08T00:00:00.000Z, 2025-10-09T00:00:00.000Z) CONSECUTIVE 3 null null null null List(0, 0) null null null null null null null List(2025-10-24T00:00:00.000Z, 2025-10-25T00:00:00.000Z) 1 day 0 null null :table null List(2025-10-23T00:00:00.000Z, 2025-10-24T00:00:00.000Z) CONSECUTIVE -4 null null null null List(0, 0) null null null null null null null List(2025-10-13T00:00:00.000Z, 2025-10-14T00:00:00.000Z) 1 day 0 null null :table null List(2025-10-12T00:00:00.000Z, 2025-10-13T00:00:00.000Z) CONSECUTIVE -39 null null null null List(0, 0) null null null null null null null List(2025-10-19T00:00:00.000Z, 2025-10-20T00:00:00.000Z) 1 day 0 null null :table null List(2025-10-18T00:00:00.000Z, 2025-10-19T00:00:00.000Z) CONSECUTIVE 4 null null null null List(0, 0) null null null null null null null List(2025-10-08T00:00:00.000Z, 2025-10-09T00:00:00.000Z) 1 day 0 null null :table null List(2025-10-07T00:00:00.000Z, 2025-10-08T00:00:00.000Z) CONSECUTIVE -6 null null null null List(0, 0) null null null null null null null List(2025-10-23T00:00:00.000Z, 2025-10-24T00:00:00.000Z) 1 day 0 null null :table null List(2025-10-22T00:00:00.000Z, 2025-10-23T00:00:00.000Z) CONSECUTIVE -3 null null null null List(0, 0) null null null null null null null List(2025-10-30T00:00:00.000Z, 2025-10-31T00:00:00.000Z) 1 day 0 null null :table null List(2025-10-29T00:00:00.000Z, 2025-10-30T00:00:00.000Z) CONSECUTIVE -4 null null null null List(0, 0) null null null null null null null List(2025-10-11T00:00:00.000Z, 2025-10-12T00:00:00.000Z) 1 day 0 null null :table null List(2025-10-10T00:00:00.000Z, 2025-10-11T00:00:00.000Z) CONSECUTIVE 49 null null null null List(0, 0) null null null null null null null List(2025-10-20T00:00:00.000Z, 2025-10-21T00:00:00.000Z) 1 day 0 null null :table null List(2025-10-19T00:00:00.000Z, 2025-10-20T00:00:00.000Z) CONSECUTIVE -49 null null null null List(0, 0) null null null null null null null List(2025-10-03T00:00:00.000Z, 2025-10-04T00:00:00.000Z) 1 day 0 null null :table null List(2025-10-02T00:00:00.000Z, 2025-10-03T00:00:00.000Z) CONSECUTIVE 75 null null null null List(0, 0) null null null null null null null List(2025-10-06T00:00:00.000Z, 2025-10-07T00:00:00.000Z) 1 day 0 null null :table null List(2025-10-05T00:00:00.000Z, 2025-10-06T00:00:00.000Z) CONSECUTIVE -39 null null null null List(0, 0) null null null null null null null List(2025-10-26T00:00:00.000Z, 2025-10-27T00:00:00.000Z) 1 day 0 null null :table null List(2025-10-25T00:00:00.000Z, 2025-10-26T00:00:00.000Z) CONSECUTIVE 3 null null null null List(0, 0) null null null null null null null List(2025-10-16T00:00:00.000Z, 2025-10-17T00:00:00.000Z) 1 day 0 null null :table null List(2025-10-15T00:00:00.000Z, 2025-10-16T00:00:00.000Z) CONSECUTIVE -19 null null null null List(0, 0) null null null null null null null List(2025-10-21T00:00:00.000Z, 2025-10-22T00:00:00.000Z) 1 day 0 null null :table null List(2025-10-20T00:00:00.000Z, 2025-10-21T00:00:00.000Z) CONSECUTIVE 9 null null null null List(0, 0) null null null null null null null List(2025-10-10T00:00:00.000Z, 2025-10-11T00:00:00.000Z) 1 day 0 null null :table null List(2025-10-09T00:00:00.000Z, 2025-10-10T00:00:00.000Z) CONSECUTIVE 8 null null null null List(0, 0) null null null null null null null List(2025-10-18T00:00:00.000Z, 2025-10-19T00:00:00.000Z) 1 day 0 null null :table null List(2025-10-17T00:00:00.000Z, 2025-10-18T00:00:00.000Z) CONSECUTIVE 49 null null null null List(0, 0) null null null null null null null List(2025-10-28T00:00:00.000Z, 2025-10-29T00:00:00.000Z) 1 day 0 null null :

Veamos las métricas de perfil calculadas para la columna «TotalPurchaseAmount». Tenga en cuenta que las métricas se calculan para toda la tabla y para cada columna individual. Analizaremos esto con más detalle al agregar métricas personalizadas.

In [0]:
display(spark.sql(f"SELECT * FROM {profile_table} where column_name = 'TotalPurchaseAmount'"))

window log_type logging_table_commit_version monitor_version granularity slice_key slice_value column_name count data_type num_nulls avg quantiles min max stddev num_zeros num_nan min_length max_length avg_length non_null_columns frequent_items median distinct_count percent_nan percent_null percent_zeros percent_distinct List(2025-10-04T00:00:00.000Z, 2025-10-05T00:00:00.000Z) INPUT 2 0 1 day null null TotalPurchaseAmount 165 float 0 5422.752726329457 List(149.97999572753906, 149.97999572753906, 149.97999572753906, 149.97999572753906, 149.97999572753906, 149.97999572753906, 149.97999572753906, 158.52999877929688, 158.52999877929688, 158.52999877929688, 158.52999877929688, 158.52999877929688, 158.52999877929688, 247.6199951171875, 247.6199951171875, 247.6199951171875, 247.6199951171875, 247.6199951171875, 247.6199951171875, 485.8399963378906, 485.8399963378906, 485.8399963378906, 485.8399963378906, 485.8399963378906, 485.8399963378906, 562.989990234375, 562.989990234375, 562.989990234375, 562.989990234375, 562.989990234375, 562.989990234375, 822.02001953125, 822.02001953125, 822.02001953125, 822.02001953125, 822.02001953125, 822.02001953125, 994.8900146484375, 994.8900146484375, 994.8900146484375, 994.8900146484375, 994.8900146484375, 994.8900146484375, 1156.8199462890625, 1156.8199462890625, 1156.8199462890625, 1156.8199462890625, 1156.8199462890625, 1156.8199462890625, 1279.1800537109375, 1279.1800537109375, 1279.1800537109375, 1279.1800537109375, 1279.1800537109375, 1279.1800537109375, 1287.1300048828125, 1287.1300048828125, 1287.1300048828125, 1287.1300048828125, 1287.1300048828125, 1287.1300048828125, 1415.1800537109375, 1415.1800537109375, 1415.1800537109375, 1415.1800537109375, 1415.1800537109375, 1415.1800537109375, 1444.8299560546875, 1444.8299560546875, 1444.8299560546875, 1444.8299560546875, 1444.8299560546875, 1444.8299560546875, 1523.8800048828125, 1523.8800048828125, 1523.8800048828125, 1523.8800048828125, 1523.8800048828125, 1523.8800048828125, 1541.1500244140625, 1541.1500244140625, 1541.1500244140625, 1541.1500244140625, 1541.1500244140625, 1541.1500244140625, 1598.5, 1598.5, 1598.5, 1598.5, 1598.5, 1598.5, 1710.8499755859375, 1710.8499755859375, 1710.8499755859375, 1710.8499755859375, 1710.8499755859375, 1710.8499755859375, 1756.7099609375, 1756.7099609375, 1756.7099609375, 1756.7099609375, 1756.7099609375, 1756.7099609375, 1756.7099609375, 1758.010009765625, 1758.010009765625, 1758.010009765625, 1758.010009765625, 1758.010009765625, 1758.010009765625, 1813.1800537109375, 1813.1800537109375, 1813.1800537109375, 1813.1800537109375, 1813.1800537109375, 1813.1800537109375, 1832.9300537109375, 1832.9300537109375, 1832.9300537109375, 1832.9300537109375, 1832.9300537109375, 1832.9300537109375, 1847.3399658203125, 1847.3399658203125, 1847.3399658203125, 1847.3399658203125, 1847.3399658203125, 1847.3399658203125, 1946.8199462890625, 1946.8199462890625, 1946.8199462890625, 1946.8199462890625, 1946.8199462890625, 1946.8199462890625, 2110.169921875, 2110.169921875, 2110.169921875, 2110.169921875, 2110.169921875, 2110.169921875, 2110.75, 2110.75, 2110.75, 2110.75, 2110.75, 2110.75, 2254.260009765625, 2254.260009765625, 2254.260009765625, 2254.260009765625, 2254.260009765625, 2254.260009765625, 2320.2900390625, 2320.2900390625, 2320.2900390625, 2320.2900390625, 2320.2900390625, 2320.2900390625, 2343.6201171875, 2343.6201171875, 2343.6201171875, 2343.6201171875, 2343.6201171875, 2343.6201171875, 2364.409912109375, 2364.409912109375, 2364.409912109375, 2364.409912109375, 2364.409912109375, 2364.409912109375, 2423.030029296875, 2423.030029296875, 2423.030029296875, 2423.030029296875, 2423.030029296875, 2423.030029296875, 2650.77001953125, 2650.77001953125, 2650.77001953125, 2650.77001953125, 2650.77001953125, 2650.77001953125, 2657.35009765625, 2657.35009765625, 2657.35009765625, 2657.35009765625, 2657.35009765625, 2657.35009765625, 2737.56005859375, 2737.56005859375, 2737.56005859375, 2737.56005859375, 2737.56005859375, 2737

### 9.6 Visualizar el panel autogenerado

Cuando finaliza el primer *refresh*, puedes ver el **dashboard autogenerado** desde la pestaña **Quality** de la tabla `silver_transactions` en el Catalog Explorer.  
Este panel muestra distintas secciones con las métricas del monitor:

1. **Volumen de datos**: Permite comprobar si el volumen de transacciones es el esperado o si ha habido variaciones por estacionalidad.  
2. **Integridad de datos**: Muestra las columnas con un alto porcentaje de valores nulos o ceros y su evolución a lo largo del tiempo.  
3. **Cambio en distribución numérica**: Detecta anomalías en variables numéricas y visualiza su rango de valores a lo largo del tiempo.  
4. **Cambio en distribución categórica**: Identifica anomalías en variables categóricas (por ejemplo, `PreferredPaymentMethod`) y muestra cómo cambia la distribución de valores con el tiempo.  
5. **Perfilado**: Permite explorar el perfil de datos numéricos y categóricos a lo largo del tiempo.

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/lhm/lhm_dashboard-1.png?raw=true" width="800px"/>


### 9.7 Investigación del Dashboard

Sin necesidad de herramientas adicionales ni configuraciones complejas, **Lakehouse Monitoring** permite perfilar, diagnosticar y controlar la calidad de los datos directamente dentro de la plataforma **Databricks Data Intelligence Platform**.

A partir del dashboard generado, podemos responder las tres preguntas iniciales:

1. **¿Qué porcentaje de valores nulos se ha introducido en esta columna? ¿Es algo normal?**  
   > En la sección *% Nulls* se observa que `PreferredPaymentMethod` pasó de un 10 % a alrededor de un 40 %.

2. **Si no es normal, ¿cuál fue la causa raíz de este problema de integridad?**  
   > En la sección *Categorical Distribution Change* vemos que tanto `PreferredPaymentMethod` como `PaymentMethod` muestran una alta deriva en la última ventana temporal.  
   > El *heatmap* revela que **Apple Pay** se añadió recientemente como nuevo valor de `PaymentMethod` al mismo tiempo que comenzaron a aparecer valores `null` en `PreferredPaymentMethod`.

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/lhm/lhm_dashboard-2.png?raw=true" width="800px" style="float:right"/>

3. **¿Qué activos posteriores podrían haberse visto afectados por este problema?**  
   > Como Lakehouse Monitoring se integra con **Unity Catalog**, puedes usar el **Lineage Graph** para identificar las tablas descendientes que han sido impactadas.

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/lhm/lhm_lineage.png?raw=true" width="800px" style="float:right"/>

Tal como se muestra en este ejemplo, puedes **detectar proactivamente los problemas de calidad antes de que afecten a los procesos posteriores**.  
Comienza a usar **Lakehouse Monitoring (General Availability)** en tu entorno